<a href="https://colab.research.google.com/github/jtlagumbay/cebqa/blob/main/retriever/bm_roberta.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **QA Pipeline**

1. ElasticSeach Indexer
2. BM25 Retriever
3. Fine-tuned XLMR Reader


# Dependencies

In [1]:
pip install elasticsearch transformers datasets evaluate rank_bm25 nltk fuzzywuzzy sentence_transformers numpy==1.26.4



[notice] A new release of pip is available: 24.2 -> 25.0.1
[notice] To update, run: python3.10 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install --upgrade --no-cache-dir numpy==1.26.4


[notice] A new release of pip is available: 24.2 -> 25.0.1
[notice] To update, run: python3.10 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install faiss-cpu


[notice] A new release of pip is available: 24.2 -> 25.0.1
[notice] To update, run: python3.10 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [4]:
pip install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cpu

Looking in indexes: https://download.pytorch.org/whl/cpu

[notice] A new release of pip is available: 24.2 -> 25.0.1
[notice] To update, run: python3.10 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')

In [5]:
from elasticsearch import Elasticsearch
from elasticsearch.helpers import bulk
import json
import os
import subprocess
import time
import pandas as pd
import requests
from transformers import pipeline, AutoModelForQuestionAnswering, AutoTokenizer, XLMRobertaTokenizerFast
from datasets import Dataset, load_dataset
import re
from evaluate import load
from rank_bm25 import BM25Okapi
from nltk.tokenize import word_tokenize
from fuzzywuzzy import fuzz
import nltk
import random
import numpy as np
from sentence_transformers import SentenceTransformer, util
import torch
from nltk.tokenize import sent_tokenize
import faiss
import unicodedata

nltk.download('punkt')
nltk.download('punkt_tab')

/usr/local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/usr/local/lib/python3.10/site-packages/fuzzywuzzy/fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/jhoannaricalagumbay/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt_tab to
[nltk_data]     /Users/jhoannaricalagumbay/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


True

In [6]:
CEBQA_DATASET = "jhoannarica/CebQuAD_fixed"
# ELASTIC_URL = "https://tender-separately-mudfish.ngrok-free.app"
# CURRENT_MODEL = "/content/drive/MyDrive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr/2025-03-15_09-36/model"
# CURRENT_TOKENIZER = "/content/drive/MyDrive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr/2025-03-15_09-36/tokenizer"
CURRENT_ROOT = "/Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07"
CURRENT_MODEL = CURRENT_ROOT+"/model"
CURRENT_TOKENIZER = CURRENT_ROOT+"/tokenizer"
ELASTIC_URL = "http://localhost:9200"
INDEX_NAME = "superbalita"
K = 3
DATASET_CSV = "/Users/jhoannaricalagumbay/School/cebqa/dataset/articles_202503120405_author_removed_fixed.csv"
BM25 = "bm25"
FAISS = "faiss"

# Indexer

Start ElasticSearch Locally:
1. Start ES docker
2. Start NGROK: `ngrok http --url=tender-separately-mudfish.ngrok-free.app 9200`


In [8]:
headers = {
    "Origin": "https://colab.research.google.com",
     "Content-Type": "application/json",
}

response = requests.options(ELASTIC_URL, headers=headers)
print(response.headers)


{'Allow': 'GET,DELETE,HEAD', 'X-elastic-product': 'Elasticsearch', 'content-type': 'text/plain; charset=UTF-8', 'content-length': '0'}


In [9]:
es = Elasticsearch([ELASTIC_URL], verify_certs=False, headers=headers)
print(es.info())
# try:
#     print(es.transport.perform_request('GET', '/'))
# except Exception as e:
#     print("Error:", e)

{'name': '40645cf85c9d', 'cluster_name': 'docker-cluster', 'cluster_uuid': 'ST_2iQqITE-zmJCo8dlrnw', 'version': {'number': '8.17.2', 'build_flavor': 'default', 'build_type': 'docker', 'build_hash': '747663ddda3421467150de0e4301e8d4bc636b0c', 'build_date': '2025-02-05T22:10:57.067596412Z', 'build_snapshot': False, 'lucene_version': '9.12.0', 'minimum_wire_compatibility_version': '7.17.0', 'minimum_index_compatibility_version': '7.0.0'}, 'tagline': 'You Know, for Search'}


In [10]:
class ElasticSearchIndexer:
    def __init__(self, index_name=INDEX_NAME):
        self.index_name = index_name
        self.es = Elasticsearch(ELASTIC_URL)  # Ensure ES is running
        print(f"Initiating ESIndexer {self.index_name}")

    def create_index(self):
        """ Create an index with a text field for BM25 """
        if not self.es.indices.exists(index=self.index_name):
            self.es.indices.create(index=self.index_name, body={
                "settings": {
                    "number_of_shards": 1,
                    "number_of_replicas": 0
                },
                "mappings": {
                    "properties": {
                        "id": {"type": "keyword"},
                        "title": {"type": "text"},
                        "body": {"type": "text"}
                    }
                }
            })
            print(f"Index '{self.index_name}' created.")

    def index_documents(self, documents):
        """ Bulk index documents into ElasticSearch """
        actions = [
            {
                "_index": self.index_name,
                "_id": doc["id"],  # Use document ID for uniqueness
                "_source": {
                    "id": doc["id"],
                    "title": doc["pseudonymized_title"],
                    "body": doc["pseudonymized_body"]
                }
            }
            for doc in documents
        ]
        bulk(self.es, actions)
        print(f"Indexed {len(documents)} documents.")

    def index_from_csv(self, file_path):
        df = pd.read_csv(file_path)
        documents = df.to_dict(orient="records")  # Convert DataFrame to a list of dicts
        self.index_documents(documents)



In [ ]:
# Sample usage
# indexer = ElasticSearchIndexer()
# indexer.create_index()
# indexer.index_from_csv("/Users/jhoannaricalagumbay/School/cebqa/dataset/articles_202503120405_author_removed_fixed.csv")

Initiating ESIndexer superbalita
Indexed 1700 documents.


# BM25

In [11]:
class BM25Retriever:
    def __init__(self, index_name="superbalita"):
        print(f"Initiating retriever with index_name: {index_name}")
        self.index_name = index_name
        self.es = Elasticsearch(ELASTIC_URL)

    def retrieve(self, query, top_k=3):
        """ Retrieve top-k relevant documents using BM25 """
        print(f"retrieving {top_k} docs for [{query}]")
        response = self.es.search(index=self.index_name, body={
            "query": {
                "match": {
                    "body": query
                }
            },
            "size": top_k
        })
        return [hit["_source"] for hit in response["hits"]["hits"]]

    def retrieve_batch(self, queries, top_k=3):
        print(f"Retrieve Batch for {len(queries)} queries")
        """ Retrieve top-k relevant documents for multiple queries using BM25 in batch mode """
        if not isinstance(queries, list):
            raise ValueError("queries should be a list of strings")

        # Multi-search request body
        request_body = ""
        for query in queries:
            request_body += f'{{"index": "{self.index_name}"}}\n'  # Metadata
            request_body += f'{{"query": {{"match": {{"body": "{query}"}}}}, "size": {top_k}}}\n'  # Query

        # Send multi-search request
        response = self.es.msearch(body=request_body)

        # Extract results
        results = []
        for query_response in response["responses"]:
            retrieved_docs = [hit["_source"] for hit in query_response["hits"]["hits"]]
            results.append(retrieved_docs)

        return results  # List of lists, where each sublist contains retrieved documents for a query

    def retrieve_batch_query_dict(self, queries_list, top_k=3):
        print(f"Retrieve Batch Dict for {len(queries_list)} queries")

        """ Retrieve top-k relevant documents for multiple queries using BM25 in batch mode.

        Args:
            queries_list (list): A list of dictionaries, each containing 'id' and 'question'.
            top_k (int): Number of top relevant documents to retrieve per query.

        Returns:
            dict: A dictionary where keys are query IDs and values are lists of retrieved documents.
        """
        if not isinstance(queries_list, list) or not all(isinstance(q, dict) and 'id' in q and 'question' in q for q in queries_list):
            raise ValueError("queries_list should be a list of dictionaries with 'id' and 'question' keys")

        # Multi-search request body
        request_body = ""
        query_ids = []  # To track IDs in order
        for query in queries_list:
            query_ids.append(query["id"])
            request_body += f'{{"index": "{self.index_name}"}}\n'  # Metadata
            request_body += f'{{"query": {{"match": {{"body": "{query["question"]}"}}}}, "size": {top_k}}}\n'  # Query

        # Send multi-search request
        response = self.es.msearch(body=request_body)

        # Extract results and associate with query IDs
        results = []
        for i, query_response in enumerate(response["responses"]):
            retrieved_docs = [hit["_source"] for hit in query_response["hits"]["hits"]]
            results.append({
                "query_id": str(query_ids[i]),
                "top_docs": retrieved_docs
            })

        return results  # Dictionary format: {id: retrieved_docs}



In [12]:
# Sample usage
retriever = BM25Retriever()
query = "kanus-a ang palarong pambansa"
top_docs = retriever.retrieve(query)
print("Retrieved Documents:", top_docs)

Initiating retriever with index_name: superbalita
retrieving 3 docs for [kanus-a ang palarong pambansa]
Retrieved Documents: [{'id': 535, 'title': 'Palaro budget gikunhoran sa P262M gikan sa P405M', 'body': 'Gitugotan ni Cebu City Acting Mayor Jhonnylou Ghen Abalayan ang pagkunhod ngadto sa P262 milyunes gikan sa P405 milyunes ang gahin alang sa Palarong Pambansa 2024 sa Hulyo. Sa press conference sa Lunes, Hunyo 3, 2024, gibutyag ni Abalayan nga dugang budget appropriations alang sa pag-host sa Palarong Pambansa ang giputol, nga naglakip sa extension sa grandstand nga gitangtang na. “I have authorized only the charging of P262 million out of the P405 million. There is a cut of P143 million,” matod ni Abalayan. Si Abalayan niingon nga ang budget alang sa pagtukod sa grandstand extension mahimo pa nga maapil sa budget appropriations sa sunod tuig. Si Abalayan niingon usab nga iyang gius-usan ang budget alang sa side events gikan sa P60 milyunes ngadto sa P20 milyunes. Siya nidugang nga 

# FAISS Indexer

In [30]:
class FAISSIndexer:
    def __init__(self, index_file="faiss_index.idx", model_name="sentence-transformers/all-MiniLM-L6-v2"):
        self.index_file = index_file
        self.model = SentenceTransformer(model_name)
        self.index = None
        self.documents = []  # Store original text
        self.index_from_csv()
        print("FAISS Indexer initialized.")

    def create_index(self, d):
        """Create a new FAISS index."""
        self.index = faiss.IndexFlatL2(d)
        print(f"Created FAISS index with dimension {d}.")

    def index_documents(self, documents):
        """Index documents into FAISS."""
        self.documents = [doc['pseudonymized_body'] for doc in documents]
        self.article_ids = [doc['id'] for doc in documents]
        self.titles = [doc['pseudonymized_title'] for doc in documents]
        
        embeddings = self.model.encode(self.documents, convert_to_numpy=True)
        d = embeddings.shape[1]
        
        if self.index is None:
            self.create_index(d)
        
        self.index.add(embeddings)
        print(f"Indexed {len(documents)} documents into FAISS.")
        self.save_index()

    def index_from_csv(self, file_path=DATASET_CSV):
        """Load documents from a CSV file and index them."""
        df = pd.read_csv(file_path)
        documents = df.to_dict(orient="records")
        self.index_documents(documents)
        
    def save_index(self):
        """Save FAISS index to disk."""
        faiss.write_index(self.index, self.index_file)
        print(f"FAISS index saved to {self.index_file}.")

    def load_index(self):
        """Load FAISS index from disk."""
        self.index = faiss.read_index(self.index_file)
        print(f"FAISS index loaded from {self.index_file}.")



In [31]:
# FAISSRetriever

In [32]:
class FAISSRetriever:
    def __init__(self, index_file="faiss_index.idx", top_k=3):
        self.indexer = FAISSIndexer(index_file=index_file)
        self.top_k = top_k

    def retrieve(self, query):
        """Retrieve top-k relevant documents using FAISS."""
        query_embedding = self.indexer.model.encode([query], convert_to_numpy=True)
        D, I = self.indexer.index.search(query_embedding, self.top_k)
        print(D, I)
        # for rank, idx in enumerate(I[0]):
        #     if idx < len(self.indexer.documents):
        #         print(self.indexer.documents[idx])
        #     else:
        #         print(f"noo {idx}")
        results = [
            {
                "rank": rank + 1,
                "score": float(D[0][rank]),
                "id": self.indexer.article_ids[idx],
                "title": self.indexer.titles[idx],
                "body": self.indexer.documents[idx],
            }
            for rank, idx in enumerate(I[0]) if idx < len(self.indexer.documents)
        ]
        return results

    def retrieve_batch(self, queries):
        print(f"processing {len(queries)}")
        """Retrieve top-k relevant documents for multiple queries."""
        query_embeddings = self.indexer.model.encode([query["question"] for query in queries], convert_to_numpy=True)
        D, I = self.indexer.index.search(query_embeddings, self.top_k)
        print(f"done {len(D)}")
        results = []
        for query_idx, query in enumerate(queries):
            print(f"query idx: {query_idx}")
            retrieved_docs = [
                {
                    "rank": rank + 1,
                    "score": float(D[query_idx][rank]),
                    "text": self.indexer.documents[idx]
                }
                for rank, idx in enumerate(I[query_idx]) if idx < len(self.indexer.documents)
            ]
            results.append({"query": query, "top_docs": retrieved_docs})
        return results


In [ ]:
# # Initialize the FAISS indexer
# indexer = FAISSIndexer(index_file="faiss_index.idx")

# Index documents from a CSV file
# # Save the FAISS index for later use
# indexer.save_index()

# indexer = FAISSIndexer(index_file="faiss_index.idx")
# indexer.load_index()

Created FAISS index with dimension 384.
Indexed 1700 documents into FAISS.
FAISS index saved to faiss_index.idx.
FAISS Indexer initialized.


In [ ]:
# Initialize the retriever with the loaded indexer
# retriever = FAISSRetriever(index_file="faiss_index.idx", top_k=K)

# # Retrieve relevant documents for a single query
# query = "kanus-a ang palarong pambansa??"
# results = retriever.retrieve(query)

# # Print retrieved documents
# print(results)


# Retrieve relevant documents for a single query
# query = [{"question": "kanus-a ang palarong pambansa?"}, {"question":"Kinsa ang hepe sa Cebu Police?"}]
# results = retriever.retrieve_batch(query)

# # Print retrieved documents
# for res in results:
#     print(res)


Created FAISS index with dimension 384.
Indexed 1700 documents into FAISS.
FAISS index saved to faiss_index.idx.
FAISS Indexer initialized.
[[0.8453598  0.89132583 0.8948861 ]] [[1399  388 1285]]
[{'rank': 1, 'score': 0.8453598022460938, 'id': 356, 'title': 'Canon: Kalampusan sa Palaro tungod nila ni Abangan, Abalayan', 'body': 'Ang kalampusan sa Palaro 2024 mahimong ma-kredito sa duha ka mga “mayor,” matod sa usa ka opisyal sa Palaro. Ang chairman sa Cebu City Sports Commission nga si Dean Canon niingon sa iyang mensahe sa SunStar Cebu niadtong Biyernes, Hulyo 19, 2024, nga si Acting Mayor Jhonnylou Ghen Abalayan nihimo na og hands-on approach, duha na lang ka bulan ang nahabilin, ug nakigtagbo sa Palaro teams kada adlaw. Samtang, ang preventively nga gisuspenso nga si Mayor Cedie Abangan, matod ni Canon, nga mao ang nangulo sa Palaro team sa miaging 18 ka mga buwan, sa wala pa ug atol sa bidding process. “We are thankful for his guidance and also for his restraint, not having “stolen

# Reader

In [16]:
class Reader:
    def __init__(
        self,
        model_path = CURRENT_MODEL,
        tokenizer_path = CURRENT_TOKENIZER
      ):
        print(f"Initiating reader with model: {model_path}")
        model_best = AutoModelForQuestionAnswering.from_pretrained(model_path)
        tokenizer_best = AutoTokenizer.from_pretrained(tokenizer_path)

        device = torch.device("mps")
        self.qa_pipeline = pipeline(
            "question-answering", 
            model=model_best, 
            tokenizer=tokenizer_best,
            device=device
            )

    def extract_answer_batch(self, queries_list, top_docs):
        print(f"Extracting batch answer for {len(queries_list)} queries")
        qa_dataset = Dataset.from_dict({
          "question": [queries_list["question"] for doc in top_docs['top_docs']] ,
          "context": [doc['body'] for doc in top_docs['top_docs']]
        })

        return self.qa_pipeline(qa_dataset)

    def extract_answer(self, question, documents, num_chunks = 1, overlap = 0.3):
        print(f"extracting answer for {question}")
        """ Find the best answer from retrieved documents while keeping metadata """
        best_result = None
        best_score = 0

        for doc in documents:
            if num_chunks == 1:
                contexts = [doc["body"]]
            else:
                contexts = self.chunk_text(doc["body"],  num_chunks, overlap)

            for context in contexts:
            #   print(question)
            #   print(context)
              result = self.qa_pipeline(question=question, context = context)
              if result["score"] > best_score:
                  best_result = {
                      "article_id": doc["id"],
                      "title": doc["title"],
                      "body": doc["body"],
                      "answer": result["answer"],
                      "score": result["score"]
                  }
                  best_score = result["score"]

        return best_result

    def chunk_text(self, text, chunk_size=3, overlap=0.5):
        sentences = sent_tokenize(text)  # Tokenize text into sentences
        step = int(chunk_size * (1 - overlap))  # Overlapping step

        chunks = []
        for i in range(0, len(sentences), step):
            chunk = sentences[i:i + chunk_size]
            if not chunk: 
                continue
            chunks.append(" ".join(chunk)) 
        
        return chunks

# QA Pipeline

In [ ]:
class QA:
    def __init__(
        self,
        model_path = CURRENT_MODEL,
        tokenizer_path = CURRENT_TOKENIZER,
        dataset = CEBQA_DATASET,
        indexer_type = BM25,
        index_name = INDEX_NAME,
        k = K,
        sample = None,
        isRandom = False,
        overlap = 0.0, 
        num_chunks = 1,
      ):
        reader = Reader(model_path=model_path, tokenizer_path=tokenizer_path)
        
        self.model_path = model_path
        self.tokenizer_path = tokenizer_path
        self.reader = reader
        self.tokenizer = XLMRobertaTokenizerFast.from_pretrained("xlm-roberta-base")
        test_dataset = load_dataset(dataset)["test"]
        self.dataset = test_dataset.filter(self.filter_incomplete_examples) \
            .map(self.normalize_row, batched=True) \
            .map(self.tokenize_train_function, batched=True)\
            .filter(self.decode_error)
        self.sentence_transformer = SentenceTransformer("all-MiniLM-L6-v2")
        self.k = k
        self.overlap = overlap
        self.num_chunks = num_chunks
        self.sample = sample
        self.isRandom = isRandom
        self.index_name = index_name
        self.indexer_type = indexer_type

        if sample is not None and isRandom:
            indices = random.sample(range(len(self.dataset)), sample)
            self.dataset = self.dataset.select(indices)
        elif sample is not None and not isRandom:
            self.dataset = self.dataset.select(range(sample))

        print(f"Initiating QA Pipeline.")
        print(f"QA model {self.model_path}")
        print(f"QA tokenizer {self.tokenizer_path}")
        print(f"QA reader {self.reader}")
        print(f"QA dataset {len(self.dataset)}")
        print(f"QA k {self.k}")
        print(f"QA overlap {self.overlap}")
        print(f"QA num_chunks {self.num_chunks}")
        print(f"QA sample {self.sample}")
        print(f"QA isRandom {self.isRandom}")
        print(f"QA index_name {self.index_name}")
        print(f"QA indexer {self.index_name}")
        self.queries = [
            {
                "id": item['id'],
                "article_id": item['article_id'],
                "question": item['question'],
                "context": {
                    "text": item['context'],
                    "start": item['context_start']
                },
                "answer": {
                    "text": item['answer'],
                    "start": item['answer_start']
                }
            }
            for item in self.dataset
        ]

        if indexer_type == BM25:
            self.retriever = BM25Retriever(index_name=index_name)
            self.run_top_docs_batch_bm25()
        else:
            self.retriever = FAISSRetriever(top_k=self.k)
            self.run_top_docs_batch_faiss()
        print(f"QA retriever {self.retriever}")
        

    def run_top_docs_batch_bm25(self):
        self.top_docs = self.retriever.retrieve_batch_query_dict(
            queries_list = self.queries,
            top_k=self.k
        )

        return self.top_docs
    
    def run_top_docs_batch_faiss(self):
        docs = []
        for item in self.dataset:
            result = retriever.retrieve(item["question"])
            doc = {
                "query_id": item["id"],
                "top_docs": result
            }
            docs.append(doc)
            
        self.top_docs = docs
        return self.top_docs

    def run(self):
        start_time = time.time()
        date_now = time.strftime('%Y-%m-%d %H:%M:%S', time.localtime(start_time))
        print(f"QA run for {self.model_path} on {date_now}")
        
        results = []

        for index, query in enumerate(self.queries):
          print(f"{index} processing {query['id']}")
          docs = self.top_docs[index]['top_docs']
        #   print([f"{doc}\n" for doc in docs])
          answer = self.reader.extract_answer(
              question = query["question"],
              documents = docs,
              num_chunks = self.num_chunks,
              overlap= self.overlap
          )
        #   print(query["answer"]["text"])
        #   print(answer["answer"])
          result = query
          result["pred"] = answer
          result["top_docs"] = docs
          results.append(result)

        self.results = results

        end_time = time.time()
        self.stats ={
            'run_time': end_time - start_time
        }
        return self.results

    def normalize_row(self, examples):
        examples["context"] = [unicodedata.normalize("NFKC", context) for context in examples["context"]]

        examples["article_body"] = [unicodedata.normalize("NFKC", body) for body in examples["article_body"]]

        examples["answer"] =  [unicodedata.normalize("NFKC", answer) for answer in examples["answer"]]

        examples["question"] = [unicodedata.normalize("NFKC", q) for q in examples["question"]]

        return examples

    def normalize_text(self, text):
        """Lowercase and remove punctuation, articles, and extra whitespace."""
        text = text.lower()
        text = re.sub(r'\W+', ' ', text)  # Remove punctuation and special characters
        text = re.sub(r'\s+', ' ', text).strip()  # Remove extra whitespace
        return text

    def compute_similarity(self, text1, text2):
        """Compute cosine similarity between two texts using Sentence Transformers."""
        emb1 = self.sentence_transformer.encode(text1, convert_to_tensor=True)
        emb2 = self.sentence_transformer.encode(text2, convert_to_tensor=True)
        similarity = util.pytorch_cos_sim(emb1, emb2).item()  # Convert tensor to float
        return similarity

    def evaluate_batch(self):
        pass

    def evaluate_retriever(self):
        wrong_doc = []
        for index, query in enumerate(self.queries):
            top_doc = self.top_docs[index]["top_docs"]
            if not any(doc["id"] == query["article_id"] for doc in top_doc):
                wrong_doc.append(query["article_id"])

        return wrong_doc

    def evaluate(self):
        print(f"QA evaluate for {len(self.results)} results on {time.strftime('%Y-%m-%d %H:%M:%S', time.localtime())}")
        pred = [
          {
              'id': result['id'],  # Convert ID to string
              'prediction_text': self.normalize_text(result['pred']['answer'])
          }
          for result in self.results
        ]

        ref = [
            {
                'id': item['id'],  # Convert ID to string
                'answers': {
                    'text': [self.normalize_text(item['answer']['text'])],
                    'answer_start': [item['answer']['start']]
                }
            }
            for item in self.results
        ]

        # Load SQuAD metric
        metric = load("squad")

        # Compute metric
        res = metric.compute(predictions=pred, references=ref)
        sentence_match_scores = [
            p['prediction_text'] in r['answers']['text'][0] for p, r in zip(pred, ref)
        ]

        # Compute average sentence match score
        avg_sentence_match = np.mean(sentence_match_scores)

        # Combine results
        res["sentence_match"] = float(avg_sentence_match )
        print(res)

        self.config = {
            'model_path': self.model_path,
            'tokenizer_path': self.tokenizer_path,
            'k': self.k,
            'sample': self.sample,
            'isRandom': self.isRandom,
            'overlap': self.overlap,
            'num_chunks': self.num_chunks,
            'indexer_type': self.indexer_type
        }
        self.eval_res = res

        return self.eval_res, self.config, self.stats
    
    def filter_incomplete_examples(self, example):
        # Ensure both "question" and "context" exist and are non-empty
        return "question" in example and example["question"] and \
            "article_body" in example and example["answer"]

    def filter_by_token_length(self, example):
        # Tokenize the concatenated question + article_body
        tokens = self.tokenizer(example["question"], example["article_body"], truncation=False)
        return len(tokens["input_ids"]) <= 512 

    def decode_error(self, example):
        input_ids = example["input_ids"]
        start_positions = example["start_positions"]
        end_positions = example["end_positions"]
        predict_answer_tokens = input_ids[start_positions : end_positions+1]
        return self.tokenizer.decode(predict_answer_tokens) == example["answer"]

    def tokenize_train_function(self, examples):
        article_text = [article for article in examples.get("article_body", [""])]
        context_text = [context for context in examples.get("context", ["{}"])]
        answer_text = examples.get("answer", [""])
        answer_start = examples.get("answer_start", [0])
        context_start_list = examples.get("context_start", [0])
        question_text = [q for q in examples.get("question", [""])]
        start_positions = []
        end_positions = []

        inputs = self.tokenizer(
            question_text,
            article_text,
            truncation="only_second",  # Truncate only the context
            max_length=512,            # Limit input length
            stride=128,                # Add a sliding window
            return_overflowing_tokens=False,  # Handle long contexts
            return_offsets_mapping=True,
            padding="max_length"
        )

        offset_mapping = inputs.pop("offset_mapping")
        # sample_map = inputs.pop("overflow_to_sample_mapping")

        for i, offset in enumerate(offset_mapping):
            answer = answer_text[i]
            context = context_text[i]
            article = article_text[i]
            start_char = int(context_start_list[i]) + int(answer_start[i])
            end_char = start_char + len(answer)


            sequence_ids = inputs.sequence_ids(i)

            # Find the start and end of the context
            idx = 0
            while sequence_ids[idx] != 1:
                idx += 1
            context_start = idx
            while sequence_ids[idx] == 1:
                idx += 1
            context_end = idx - 1

            # If the answer is not fully inside the context, label is (0, 0)
            if offset[context_start][0] > start_char or offset[context_end][1] < end_char:
                start_positions.append(0)
                end_positions.append(0)
            else:
                # Otherwise it's the start and end token positions
                idx = context_start
                while idx <= context_end and offset[idx][0] <= start_char:
                    idx += 1
                start_positions.append(idx - 1)

                idx = context_end
                while idx >= context_start and offset[idx][1] >= end_char:
                    idx -= 1
                end_positions.append(idx + 1)

        inputs["start_positions"] = start_positions
        inputs["end_positions"] = end_positions


        return inputs


# QA - BM25

In [126]:
print(np.__version__)  # Check if NumPy is available
print(torch.randn(1).numpy()) 


1.26.4
[-0.11015862]


In [34]:
qa_bm25 = QA(
    model_path=CURRENT_MODEL,
    k = 1, overlap=0.0, num_chunks=1)
wrong = qa_bm25.evaluate_retriever()
print(len(wrong))

Initiating reader with model: /Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07/model


Filter: 100%|██████████| 5526/5526 [00:02<00:00, 2361.23 examples/s]


Initiating QA Pipeline.
QA model /Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07/model
QA tokenizer /Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07/tokenizer
QA reader <__main__.Reader object at 0x1d1bc66e0>
QA dataset 4141
QA k 1
QA overlap 0.0
QA num_chunks 1
QA sample None
QA isRandom False
QA index_name superbalita
QA indexer superbalita
Initiating retriever with index_name: superbalita
Retrieve Batch Dict for 4141 queries
QA retriever <__main__.BM25Retriever object at 0x1d49a2650>
1500


In [ ]:
qa_bm25.run()

QA run for /Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07/model on 2025-04-01 20:55:57
0 processing 01437-013
extracting answer for Kinsa ang ig-agaw nga giatake sa sawa?
1 processing 01130-018
extracting answer for Unsay gibuhat ni Brent Idica pagkahuman sa insidente?
2 processing 00437-006
extracting answer for Unsa nga mga distrito ang giila sa dakbayan?
3 processing 00101-004
extracting answer for Kanus-a mobalik sa normal nga operasyon ang mga biyahe?
4 processing 00139-012
extracting answer for Asa naggikan si Helena?
5 processing 00184-010
extracting answer for Unsa ang epekto sa commercial flight sa ekonomiya sa turismo sa Bantayan Island?
6 processing 00206-016
extracting answer for Unsa ang ngalan sa rehabilitation facility nga na-imbestigahan?
7 processing 01043-002
extracting answer for Kinsa ang nagpatuman og hugot nga seguridad sa mga tourist desti

[{'id': '01437-013',
  'question': 'Kinsa ang ig-agaw nga giatake sa sawa?',
  'context': {'text': 'Si Apple Cutie, kinsa nahinabi sa Superbalita Cebu sa Biyernes, Disyembre 1, niasoy nga ang sawa gigukod sa banakon hangtod nga nisulod sa payag sa iyang ig-agaw nga si Imee Niu.',
   'start': 262},
  'answer': {'text': 'si Imee Niu', 'start': 166},
  'pred': {'article_id': 1437,
   'title': 'Banakon, sawa gaaway, gipatay',
   'body': 'Usa ka dakong banakon ug gamay nga sawa ang nag-away sa su’d sa usa ka payag sa Barangay Lamacan, lungsod sa Sibonga, ala 1 sa hapon sa Huwebes, Nobiyembre 30, 2023. Apan ang duka ka halas gitigbas-patay sa tagbalay tungod sa ilang kahadlok sa kaagresibo niini. Si Apple Cutie, kinsa nahinabi sa Superbalita Cebu sa Biyernes, Disyembre 1, niasoy nga ang sawa gigukod sa banakon hangtod nga nisulod sa payag sa iyang ig-agaw nga si Imee Niu. Ang duha ka mga bitin dali’ng gitigbas sa bana sa naulahi nga si Godfrey. Matod pa, ang balay sa magtiayong Niul duol sa 

In [ ]:
qa_bm25.evaluate()


QA evaluate for 4141 results on 2025-04-01 21:58:49
{'exact_match': 36.295580777589954, 'f1': 52.20597110424398, 'sentence_match': 0.47452306206230377}


({'exact_match': 36.295580777589954,
  'f1': 52.20597110424398,
  'sentence_match': 0.47452306206230377},
 {'model_path': '/Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07/model',
  'tokenizer_path': '/Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr/2025-03-15_09-36/tokenizer',
  'k': 1,
  'sample': None,
  'isRandom': False,
  'overlap': 0.0,
  'num_chunks': 1,
  'indexer_type': 'bm25'},
 {'run_time': 3712.801553964615})

# QA - FAISS

In [35]:
qa_faiss = QA(
    model_path=CURRENT_MODEL,
    k = 1, overlap=0.0, num_chunks=1,
    indexer_type=FAISS)
wrong_faiss = qa_faiss.evaluate_retriever()
print(len(wrong_faiss))

Initiating reader with model: /Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07/model


Filter: 100%|██████████| 5526/5526 [00:02<00:00, 2481.75 examples/s]


Initiating QA Pipeline.
QA model /Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07/model
QA tokenizer /Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07/tokenizer
QA reader <__main__.Reader object at 0x1d487ce80>
QA dataset 4141
QA k 1
QA overlap 0.0
QA num_chunks 1
QA sample None
QA isRandom False
QA index_name superbalita
QA indexer superbalita
Created FAISS index with dimension 384.
Indexed 1700 documents into FAISS.
FAISS index saved to faiss_index.idx.
FAISS Indexer initialized.
retrieving 3 docs for [Kinsa ang ig-agaw nga giatake sa sawa?]
retrieving 3 docs for [Unsay gibuhat ni Brent Idica pagkahuman sa insidente?]
retrieving 3 docs for [Unsa nga mga distrito ang giila sa dakbayan?]
retrieving 3 docs for [Kanus-a mobalik sa normal nga ope

[[{'rank': 1,
   'score': 0.5970975756645203,
   'id': 1106,
   'title': 'Liog sa sawa gipunggot human nakatukob og himuangan sa Balamban',
   'body': 'Sawa nga nikaon og himungaan sa Martes sa buntag, Pebrero 6, 2024 sa sityo Butong, Brgy. Buanoy, Balamban gilunggoan og ulo. Matod pa ni Doris Lubguban Mabuting, tag-iya sa hulagway nga gi post sa Facebook diin makita ang mga bata nga nagkupot sa dako nga patay na nga sawa, nga ila ning nakit-an mga alas 6 sa Martes sa buntag. Didto kini sa ilang bakante nga luna gilabay human gilunggoan og ulo. Ilang nasayran nga nikaon kini og himungaan sa ilang silingan apan wa sila nakaila kinsa ang nipunggot sa ulo sa sawa. Ang pagpatay sa usa ka wildlife, sama sa sawa, gidili sa balaod, gawas kon hulga kini sa kinabuhi sa usa ka tawo. Nalatid kini sa Wildlife Resources Conservation and Protection Act. Ning nakalabay nga mga adlaw, nag trending sa social media ang Banakon o King cobra ug sawa. Ang mga bitin gipatay, inay gi-rescue.'},
  {'rank': 2,

In [36]:
qa_faiss.run()
qa_faiss.evaluate()

QA run for /Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07/model on 2025-04-02 05:14:33
0 processing 01437-013
extracting answer for Kinsa ang ig-agaw nga giatake sa sawa?
1 processing 01130-018
extracting answer for Unsay gibuhat ni Brent Idica pagkahuman sa insidente?
2 processing 00437-006
extracting answer for Unsa nga mga distrito ang giila sa dakbayan?
3 processing 00101-004
extracting answer for Kanus-a mobalik sa normal nga operasyon ang mga biyahe?
4 processing 00139-012
extracting answer for Asa naggikan si Helena?
5 processing 00184-010
extracting answer for Unsa ang epekto sa commercial flight sa ekonomiya sa turismo sa Bantayan Island?
6 processing 00206-016
extracting answer for Unsa ang ngalan sa rehabilitation facility nga na-imbestigahan?
7 processing 01043-002
extracting answer for Kinsa ang nagpatuman og hugot nga seguridad sa mga tourist desti

({'exact_match': 29.147548901231588,
  'f1': 42.2781343629778,
  'sentence_match': 0.34943250422603234},
 {'model_path': '/Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07/model',
  'tokenizer_path': '/Users/jhoannaricalagumbay/Library/CloudStorage/GoogleDrive-jtlagumbay@up.edu.ph/My Drive/UP Files/IV - 2nd sem/CMSC 198.1/cebqa_roberta/xlmr_body-filtered/2025-04-01_12-07/tokenizer',
  'k': 1,
  'sample': None,
  'isRandom': False,
  'overlap': 0.0,
  'num_chunks': 1,
  'indexer_type': 'faiss'},
 {'run_time': 7760.772953033447})